# Problem Statement
Perform topic modelling using the 20 Newsgroup dataset (the dataset is also available in
sklearn datasets sub-module). Perform the required data cleaning steps using NLP and then
model the topics
1. Using Latent Dirichlet Allocation (LDA).
2. Using Probabilistic Latent Semantic Analysis (PLSA)

PLSA or Probabilistic Latent Semantic Analysis is a technique used to model
information under a probabilistic framework. It is a statistical technique for the analysis of
two-mode and co-occurrence data. PLSA characterizes each word in a document as a
sample from a mixture model, where mixture components are conditionally independent
multinomial distributions. Its main goal is to model cooccurrence information under a
probabilistic framework in order to discover the underlying semantic structure of the data.

# About Dataset :- 
    
    This dataset contain collection of newsgroup of different Topic there are total 20 Topic related news in the dataset but we will consider only 7 to 8 Topic in the case beacuse it takes lots of time in preprocessing

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.decomposition import NMF
from sklearn.preprocessing import normalize

In [2]:
categories = ['alt.atheism', 'talk.religion.misc','comp.graphics', 'sci.space', 'sci.med','sci.space','soc.religion.christian']
newsgroups_train = fetch_20newsgroups(subset='train',categories=categories)

In [3]:
newsgroups_train

{'data': ['From: schumach@convex.com (Richard A. Schumacher)\nSubject: Re: DC-X update???\nNntp-Posting-Host: starman.convex.com\nOrganization: CONVEX Computer Corporation, Richardson, Tx., USA\nX-Disclaimer: This message was written by a user at CONVEX Computer\n              Corp. The opinions expressed are those of the user and\n              not necessarily those of CONVEX.\nLines: 32\n\nIn <1993Apr15.234154.23145@iti.org> aws@iti.org (Allen W. Sherzer) writes:\n\n>As for the future, there is at least $5M in next years budget for work\n>on SSRT. They (SDIO) have been looking for more funds and do seem to have\n>some. However, SDIO is not (I repeat, is not) going to fund an orbital\n>prototype. The best we can hope from them is to 1) keep it alive for\n>another year, and 2) fund a suborbital vehicle which MIGHT (with\n>major modifications) just make orbit. There is also some money for a\n>set of prototype tanks and projects to answer a few more open questions.\n\nWould the sub-orbit

In [4]:
from pprint import pprint
#pprint(list(newsgroups_train.target_names))
print(len(list(newsgroups_train.target_names)))

7


In [5]:
newsgroups_train.data

['From: schumach@convex.com (Richard A. Schumacher)\nSubject: Re: DC-X update???\nNntp-Posting-Host: starman.convex.com\nOrganization: CONVEX Computer Corporation, Richardson, Tx., USA\nX-Disclaimer: This message was written by a user at CONVEX Computer\n              Corp. The opinions expressed are those of the user and\n              not necessarily those of CONVEX.\nLines: 32\n\nIn <1993Apr15.234154.23145@iti.org> aws@iti.org (Allen W. Sherzer) writes:\n\n>As for the future, there is at least $5M in next years budget for work\n>on SSRT. They (SDIO) have been looking for more funds and do seem to have\n>some. However, SDIO is not (I repeat, is not) going to fund an orbital\n>prototype. The best we can hope from them is to 1) keep it alive for\n>another year, and 2) fund a suborbital vehicle which MIGHT (with\n>major modifications) just make orbit. There is also some money for a\n>set of prototype tanks and projects to answer a few more open questions.\n\nWould the sub-orbital versio

In [6]:
len(newsgroups_train.filenames)

3227

In [8]:
import nltk
import re

In [9]:
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem import WordNetLemmatizer
ps = PorterStemmer()

# Preprocessing the Data 

In [10]:
corpus = []
lem = WordNetLemmatizer()
for i in range(0,len(newsgroups_train.filenames)):
    review = newsgroups_train.data[i].split()
    review = [lem.lemmatize(word) for word in review if word not in set(stopwords.words('english'))]
    review = ' '.join(review)
    corpus.append(review)

In [11]:
vectorizer = CountVectorizer(max_features=5000)
x_counts = vectorizer.fit_transform(corpus)

In [12]:
transformer = TfidfTransformer()
x_tfidf = transformer.fit_transform(x_counts)

In [13]:
xtfidf_norm = normalize(x_tfidf, norm='l1', axis=1)

In [14]:
#number of topics
num_topics=7
#obtain a NMF model.
model = NMF(n_components=num_topics, init='nndsvd')
#fit the model
model.fit(xtfidf_norm)

NMF(init='nndsvd', n_components=7)

In [15]:
def get_nmf_topics(model, n_top_words):
    
    #the word ids obtained need to be reverse-mapped to the words so we can print the topic names.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {}
    for i in range(num_topics):
        
        #for each topic, obtain the largest values, and add the words they map to into the dictionary.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words
    
    return pd.DataFrame(word_dict)

In [16]:
get_nmf_topics(model, 30)

Topic # 01  Topic # 02    Topic # 03  Topic # 04    Topic # 05  \
0          god        pitt           edu         ___         petch   
1          the         geb    university          __         grass   
2          edu      gordon        thanks         uni        valley   
3          com       banks       subject          de         chuck   
4           it          cs          from      baalke           tek   
5          one         edu          file        ____         daily   
6       people  pittsburgh         lines     polygon         verse   
7        jesus       cadre  organization   reduction            ca   
8           in         dsl       posting         jpl         group   
9        would    shameful          nntp       _____           com   
10         you       n3jxp          host    surfaces          love   
11          re    chastity            ac      kelvin         lines   
12          he   surrender            uk          49          from   
13   christian   intellect        anyone   algorithm       subject   
14      writes  skepticism      graphics     glasgow       whoever   
15         say        univ        please      scodal         faith   
16       bible        soon       program    siggraph  organization   
17     believe    computer         image         ron            16   
18     article     science       looking        5000       matthew   
19       think       reply       graphic         jet        heaven   
20     sandvik     article          help         192        romans   
21         and          to          mail  propulsion            18   
22        that          in        format   computing            12   
23          if      writes          know     germany    revelation   
24        this        lyme            ca          92        proper   
25  christians    migraine       polygon         gov        deeply   
26        know          re   information       media          lord   
27        like         com          card        dept          show   
28        from       blood          need      bitmap           son   
29      church     patient       windows    keywords           god   

        Topic # 06  Topic # 07  
0             nasa       keith  
1            space     caltech  
2           access         sgi  
3              gov     livesey  
4            digex         edu  
5            henry     solntze  
6           egalon         wpd  
7              pat   schneider  
8          toronto         cco  
9           alaska    morality  
10             com       allan  
11            larc         jon  
12             net    atheists  
13             zoo         com  
14             prb   objective  
15        oliveira   political  
16            moon    pasadena  
17           orbit        nntp  
18          aurora  california  
19         spencer     posting  
20         posting        host  
21  communications   institute  
22            nntp      writes  
23             jpl  technology  
24            host      mathew  
25          online    punisher  
26             edu        cwru  
27         express       moral  
28           nsmca         gap  
29         zoology          re

In [17]:
np.sort(model.components_[0])[::-1]

array([0.2912109 , 0.18668383, 0.18347002, ..., 0.        , 0.        ,
       0.        ])

In [22]:
#number of topics
num_topics=7
#obtain a LDA 
model.
model = LatentDirichletAllocation(n_components=num_topics)
#fit the model
model.fit(xtfidf_norm)

LatentDirichletAllocation(n_components=7)

In [23]:
def get_lda_topics(model, n_top_words):
    
    #the word ids obtained need to be reverse-mapped to the words so we can print the topic names.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {}
    for i in range(num_topics):
        
        #for each topic, obtain the largest values, and add the words they map to into the dictionary.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words
    
    return pd.DataFrame(word_dict)

In [24]:
get_lda_topics(model, 30)

Topic # 01    Topic # 02  Topic # 03   Topic # 04   Topic # 05  \
0          542           edu       petch      op_rows        halat   
1          706           com       grass      op_cols       egalon   
2        n4tmi           the      valley          row      almanac   
3         0358          from       chuck          int        bears   
4        30602       subject       daily          col     oliveira   
5         7415  organization      sister      catalog         pooh   
6           p3         lines      deeply        noise           jb   
7           p1            it     whoever      steinly         frog   
8     mcovingt            in       verse        topaz         larc   
9           ai            re        gold     operator      langley   
10          p2           god       honor  improvement  substantial   
11         den         would    greatest         7415    surrender   
12   covington           one       cover         0358    beautiful   
13          pi    university      proper        n4tmi    rejection   
14        pole        writes         tek        30602      precise   
15      aisun3       article        sins        terms    americans   
16      nicely       posting  revelation          706         ring   
17          85          nntp      wisdom          542          245   
18   associate          host       above          cat       stable   
19      radius          know      romans          bih    organized   
20     steinly            cs     steinly          300   television   
21       topaz        people       topaz          zoo      planned   
22  artificial          this     brother      almanac      johnson   
23         thu          like     matthew       errors      sending   
24         int            to     kingdom           p3          604   
25      unlike            if        7415      zisfein     combined   
26      gained         space      choose        input     sometime   
27     amateur            is       n4tmi         rind    precisely   
28         bih           you        0358        utzoo      steinly   
29      athens         think       30602       remove        topaz   

     Topic # 06  Topic # 07  
0       zisfein      gordon  
1           wpi       banks  
2       factory         geb  
3           212       henry  
4            dn         zoo  
5   polytechnic   surrender  
6       steinly   intellect  
7         topaz  skepticism  
8          todd       n3jxp  
9       glucose    chastity  
10      tension       cadre  
11        motor         dsl  
12  electronics    shameful  
13         7415     zoology  
14        helps       pyron  
15         0358        rind  
16        n4tmi        cray  
17        30602        dseg  
18        front       utzoo  
19     includes     toronto  
20      minimal         bih  
21        under     kipling  
22        upset      skndiv  
23          542     steinly  
24          706       topaz  
25     weakness  enterprise  
26          bih        pitt  
27     occurred     spencer  
28         meal      median  
29          zoo  sigurdsson